In [1]:
!pip install plotly==4.5
!pip install xlsxwriter

     |████████████████████████████████| 7.1MB 7.9MB/s 
  Found existing installation: plotly 4.4.1
    Uninstalling plotly-4.4.1:
      Successfully uninstalled plotly-4.4.1
     |████████████████████████████████| 153kB 9.4MB/s 


In [2]:
import pandas as pd
import plotly.express as px
import json
import datetime

In [9]:
sheets = pd.read_excel('coviprev-vague23.xlsx', sheet_name=None)

In [10]:
# Remove useless cols and rows 
for sheet in sheets.values():
    sheet.drop(['ps12mois', 'ps12mois_inf', 'ps12mois_sup'], axis=1, inplace=True)
    sheet.drop(['anxiete_inf', 'anxiete_sup', 'depression_inf', 'depression_sup', 'pbsommeil_inf', 'pbsommeil_sup'], axis=1, inplace=True)
    sheet.dropna(inplace=True)
    sheet.rename(columns={'semaine': 'date'}, inplace=True)

In [12]:
# Replace dates
mapping = {'janv': '1',
           'fév': '2', 'fev': '2',
           'mars': '3',
           'avr': '4', 'avril': '4',
           'mai': '5',
           'juin': '6',
           'juillet': '7',
           'août': '8',
           'sept': '9',
           'oct': '10',
           'nov': '11',
           'dec': '12'}

def transform_date(string):
    vague = int(string.split(' ')[1])
    annee = '2021' if vague >= 20 else '2020'
    jour, mois = string.split('-')[-1].replace('.', '').split(' ')
    mois = mapping[mois].zfill(2)
    date = annee + '/' + mois + '/' + jour.zfill(2)
    return date

for sheet in sheets.values():
    sheet['date'] = sheet['date'].apply(transform_date)

In [13]:
# Sort dataframes indexes
sheets['fra'].sort_values(['date', 'fra'], inplace=True)
sheets['fra'].reset_index(drop=True, inplace=True)

sheets['age'].sort_values(['date', 'age'], inplace=True)
sheets['age'].reset_index(drop=True, inplace=True)

sheets['sexe'].sort_values(['date', 'sexe'], inplace=True)
sheets['sexe'].reset_index(drop=True, inplace=True)

sheets['reg'].sort_values(['date', 'reg'], inplace=True)
sheets['reg'].reset_index(drop=True, inplace=True)

In [16]:
# Replace code region by name and rename column reg
sheets['reg'].rename(columns={'reg': 'region'}, inplace=True)

regions_name = pd.read_csv('metadata-coviprev-libelle-region.csv', sep=';').set_index('Code')
sheets['reg']['region'] = regions_name.loc[sheets['reg']['region']].values

In [17]:
for crit, sheet in sheets.items():
    if crit != 'reg':
        sheet['date'] = sheet['date'].apply(lambda x: datetime.datetime.strptime(x, '%Y/%m/%d'))

In [18]:
sheets['fra'].head(3)

fra       date  anxiete  depression  pbsommeil
0  fr 2020-04-01     21.5        19.9       61.3
1  fr 2020-04-16     18.1        17.6       63.7
2  fr 2020-04-22     18.9        20.4       66.8

In [19]:
sheets['age'].tail(3)

age       date  anxiete  depression  pbsommeil
107       35-49 ans 2021-04-23     24.6        25.3       65.6
108       50-64 ans 2021-04-23     16.7        21.7       62.5
109  65 ans et plus 2021-04-23     15.0        16.3       59.3

In [20]:
sheets['sexe'].tail(3)

sexe       date  anxiete  depression  pbsommeil
41  Homme 2021-03-17     16.2        18.4       59.5
42  Femme 2021-04-23     25.9        24.3       69.6
43  Homme 2021-04-23     18.3        19.6       58.0

In [21]:
sheets['reg'].head(12)

region        date  anxiete  depression  pbsommeil
0                Île-de-France  2020/04/01     19.4        20.6       63.5
1          Centre-Val de Loire  2020/04/01     22.4        27.7       61.7
2      Bourgogne-Franche-Comté  2020/04/01     17.6        17.8       55.0
3                    Normandie  2020/04/01     22.8        19.0       60.9
4              Hauts-de-France  2020/04/01     22.6        16.4       64.9
5                    Grand-Est  2020/04/01     26.4        25.2       60.5
6             Pays de la Loire  2020/04/01     17.9        14.6       57.2
7                     Bretagne  2020/04/01     19.3        21.4       63.3
8           Nouvelle-Aquitaine  2020/04/01     17.9        17.8       60.1
9                    Occitanie  2020/04/01     26.1        23.5       58.1
10        Auvergne-Rhône-Alpes  2020/04/01     22.9        18.5       62.2
11  Provence-Alpes-Côte d'Azur  2020/04/01     21.6        17.2       61.7

In [28]:
px.area(sheets['fra'], x='date', y='anxiete')

In [30]:
px.line(sheets['age'], x='date', y='anxiete', color='age')

In [31]:
px.line(sheets['sexe'], x='date', y='anxiete', color='sexe')

In [26]:
with open('france-regions.geojson', 'r') as f:
    france = eval(f.read())
    # france['features'][5]['properties']['nom'] = 'Grand-Est'

px.choropleth_mapbox(sheets['reg'], 
    geojson=france, 
    locations='region', 
    color='depression',
    featureidkey='properties.nom',
    mapbox_style="carto-positron",
    animation_frame='date',
    color_continuous_scale='Reds',
    range_color=(0, 50),
    opacity=0.5,
    zoom=4.5, 
    center={"lat": 46.71109, "lon": 1.7191036})
    # title=titles[cible],
    # labels=dict(zip(targets, 
                # [label + ' (%)' for label in labels])))

In [27]:
writer = pd.ExcelWriter('coviprev23.xlsx', engine='xlsxwriter')

for name, sheet in sheets.items():
    sheet.to_excel(writer, index=False, sheet_name=name)

writer.save()

In [ ]:
with open('france-regions.geojson', 'w') as f:
    json.dump(france, f)